In [42]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import re
import timeit
import datetime
import xgboost as xgb
import math
import plotly.express as px
import pandas as pd
import plotly.graph_objects as go
import plotly.io as pio
import plotly.graph_objs as go
import folium
import json
import utm
import scipy
from plotly.offline import init_notebook_mode, iplot
init_notebook_mode(connected=True)
import joblib
import seaborn as sns
from sklearn.ensemble import IsolationForest
from sklearn.cluster import KMeans
import folium
from __future__ import print_function
from ipywidgets import interact, interactive, fixed, interact_manual, Layout
import ipywidgets as widgets
import datetime

# libraries for import all file names
from prettytable import PrettyTable
from os import listdir
from os.path import isfile, join
import statsmodels.api as sm
from statsmodels.tsa.seasonal import seasonal_decompose
from sklearn.model_selection import TimeSeriesSplit, GridSearchCV
from sklearn.metrics import accuracy_score , mean_squared_error
from sklearn.ensemble import RandomForestRegressor, ExtraTreesRegressor
from yellowbrick.model_selection import FeatureImportances
from sklearn.linear_model import LinearRegression



# Funcions auxiliars

In [40]:
#Funció per poder mostrar i ocultar cel.les (per fer el notebook més llegible)
from IPython.display import HTML
import random

def hide_toggle(for_next=False):
    this_cell = """$('div.cell.code_cell.rendered.selected')"""
    next_cell = this_cell + '.next()'

    toggle_text = 'Toggle show/hide'  # text shown on toggle link
    target_cell = this_cell  # target cell to control with toggle
    js_hide_current = ''  # bit of JS to permanently hide code in current cell (only when toggling next cell)

    if for_next:
        target_cell = next_cell
        toggle_text += ' next cell'
        js_hide_current = this_cell + '.find("div.input").hide();'

    js_f_name = 'code_toggle_{}'.format(str(random.randint(1,2**64)))

    html = """
        <script>
            function {f_name}() {{
                {cell_selector}.find('div.input').toggle();
            }}

            {js_hide_current}
        </script>

        <a href="javascript:{f_name}()">{toggle_text}</a>
    """.format(
        f_name=js_f_name,
        cell_selector=target_cell,
        js_hide_current=js_hide_current, 
        toggle_text=toggle_text
    )

    return HTML(html)

# Visualització Geografica

In [7]:
#Funció visualització estacions SMC i AMC

def prepareMap():  
    m = folium.Map(location=[41.96867, 2.41404], zoom_start=10)

    tooltip = ''
    #Dades SMC
    folium.Marker(
        [42.07398, 2.20862], popup="<i>CC (Oris)</i>", tooltip=tooltip, icon=folium.Icon(icon="umbrella", prefix='fa')
    ).add_to(m)
    folium.Marker(
        [42.37717, 2.41456], popup="<i>CG (Molló - Fabert)</i>", tooltip=tooltip, icon=folium.Icon(icon="umbrella", prefix='fa')
    ).add_to(m)
    folium.Marker(
        [42.25839, 2.36429 ], popup="<i>CI (Sant Pau de Següries)</i>", tooltip=tooltip, icon=folium.Icon(icon="umbrella", prefix='fa')
    ).add_to(m)
    folium.Marker(
        [41.87813, 2.17873 ], popup="<i>CY (Muntanyola)</i>", tooltip=tooltip, icon=folium.Icon(icon="umbrella", prefix='fa')
    ).add_to(m)
    folium.Marker(
        [42.39848, 2.15517 ], popup="<i>DG (Nuria)</i>", tooltip=tooltip, icon=folium.Icon(icon="umbrella", prefix='fa')
    ).add_to(m)
    folium.Marker(
        [42.11653, 2.78969 ], popup="<i>DJ (Banyoles)</i>", tooltip=tooltip, icon=folium.Icon(icon="umbrella", prefix='fa')
    ).add_to(m)
    folium.Marker(
        [41.96095, 2.63108 ], popup="<i>DN (Anglès)</i>", tooltip=tooltip, icon=folium.Icon(icon="umbrella", prefix='fa')
    ).add_to(m)
    folium.Marker(
        [41.96867, 2.41404 ], popup="<i>KE (Pantà de Sau)</i>", tooltip=tooltip, icon=folium.Icon(icon="umbrella", prefix='fa')
    ).add_to(m)
    folium.Marker(
        [42.22189, 2.2427 ], popup="<i>M6 (Sant Joan de les Abadesses)</i>", tooltip=tooltip, icon=folium.Icon(icon="umbrella", prefix='fa')
    ).add_to(m)
    folium.Marker(
        [42.05398, 3.06195 ], popup="<i>UB ('La Tallada d'Empordà)</i>", tooltip=tooltip, icon=folium.Icon(icon="umbrella", prefix='fa')
    ).add_to(m)
    folium.Marker(
        [41.87449, 2.92694 ], popup="<i>UN (Cassà de la Selva)</i>", tooltip=tooltip, icon=folium.Icon(icon="umbrella", prefix='fa')
    ).add_to(m)
    folium.Marker(
        [41.91461, 2.82069 ], popup="<i>UO (Fornells de la Selva)</i>", tooltip=tooltip, icon=folium.Icon(icon="umbrella", prefix='fa')
    ).add_to(m)
    folium.Marker(
        [41.95224, 2.23271], popup="<i>V3 (Gurb)</i>", tooltip=tooltip, icon=folium.Icon(icon="umbrella", prefix='fa')
    ).add_to(m)
    folium.Marker(
        [42.11477, 2.21483 ], popup="<i>V4 (Montesquiu)</i>", tooltip=tooltip, icon=folium.Icon(icon="umbrella", prefix='fa')
    ).add_to(m)
    folium.Marker(
        [41.88244, 2.21483 ], popup="<i>VN (Vilobí d'Onyar)</i>", tooltip=tooltip, icon=folium.Icon(icon="umbrella", prefix='fa')
    ).add_to(m)
    folium.Marker(
        [41.84008, 2.41877 ], popup="<i>WS (Viladrau)</i>", tooltip=tooltip, icon=folium.Icon(icon="umbrella", prefix='fa')
    ).add_to(m)
    folium.Marker(
        [42.03947, 2.11993 ], popup="<i>V5 (Perafita)</i>", tooltip=tooltip, icon=folium.Icon(icon="umbrella", prefix='fa')
    ).add_to(m)
    
    #Dades ACA (les coordenades están en format UTM, truquem una funció per pasarles a longitud - latitud)
    folium.Marker(
        utm.to_latlon(439144, 4655539, 31, 'northern'), popup="<i>Torrelló-Ges (F009891) </i>", tooltip=tooltip, icon=folium.Icon(color='red', icon="dashboard", prefix='fa')
    ).add_to(m)
    folium.Marker(
        utm.to_latlon(442102, 4648259, 31, 'northern'), popup="<i>Masies de Roda (L08116-72-00002) </i>", tooltip=tooltip, icon=folium.Icon(color='red', icon="dashboard", prefix='fa')
    ).add_to(m)
    folium.Marker(
        utm.to_latlon(439144, 4669209, 31, 'northern'), popup="<i>Ripoll (L17147-72-00005) </i>", tooltip=tooltip, icon=folium.Icon(color='red', icon="dashboard", prefix='fa')
    ).add_to(m)
    folium.Marker(
        utm.to_latlon(437546, 4674665, 31, 'northern'), popup="<i>Sant Joan de les Abadesses (L17167-72-00001) </i>", tooltip=tooltip, icon=folium.Icon(color='red', icon="dashboard", prefix='fa')
    ).add_to(m)
    folium.Marker(
        utm.to_latlon(469379, 4645530, 31, 'northern'), popup="<i>Anglès (F014672) </i>", tooltip=tooltip, icon=folium.Icon(color='red', icon="dashboard", prefix='fa')
    ).add_to(m)
    folium.Marker(
        utm.to_latlon(477269, 4651536, 31, 'northern'), popup="<i>Ginestar-Llemena (F000005) </i>", tooltip=tooltip, icon=folium.Icon(color='red', icon="dashboard", prefix='fa')
    ).add_to(m)
    folium.Marker(
        utm.to_latlon(484973, 4638465, 31, 'northern'), popup="<i>Campllong-Gotarra (L17038-72-00002)</i>", tooltip=tooltip, icon=folium.Icon(color='red', icon="dashboard", prefix='fa')
    ).add_to(m)
    folium.Marker(
        utm.to_latlon(485464, 4647022, 31, 'northern'), popup="<i>Girona-Onyar (L17079-72-00004) </i>", tooltip=tooltip, icon=folium.Icon(color='red', icon="dashboard", prefix='fa')
    ).add_to(m)
    folium.Marker(
        utm.to_latlon(484777, 4638503, 31, 'northern'), popup="<i>Riudellots-Onyar (F026458) </i>", tooltip=tooltip, icon=folium.Icon(color='red', icon="dashboard", prefix='fa')
    ).add_to(m)
    folium.Marker(
        utm.to_latlon(499269, 4658310, 31, 'northern'), popup="<i>Colomers (L17055-72-00002 	) </i>", tooltip=tooltip, icon=folium.Icon(color='red', icon="dashboard", prefix='fa')
    ).add_to(m)
    folium.Marker(
        utm.to_latlon(439144, 4648705, 31, 'northern'), popup="<i>Girona-Ter (L17079-72-00005) </i>", tooltip=tooltip, icon=folium.Icon(color='red', icon="dashboard", prefix='fa')
    ).add_to(m)
    folium.Marker(
        utm.to_latlon(467132, 4648235, 31, 'northern'), popup="<i>Pasteral-Cabal (F001242) </i>", tooltip=tooltip, icon=folium.Icon(color='red', icon="dashboard", prefix='fa')
    ).add_to(m)
    folium.Marker(
        utm.to_latlon(510378, 4653688, 31, 'northern'), popup="<i>Torroella de Montgrí (L17199-72-00001) </i>", tooltip=tooltip, icon=folium.Icon(color='red', icon="dashboard", prefix='fa')
    ).add_to(m)
    folium.Marker(
        utm.to_latlon(483379, 4660993, 31, 'northern'), popup="<i>Conellà Terri (F001243) </i>", tooltip=tooltip, icon=folium.Icon(color='red', icon="dashboard", prefix='fa')
    ).add_to(m)
    
    #Outline del Riu Ter
    folium.GeoJson(json.load(open("ter.geojson")), name="Riu Ter").add_to(m)
    
    return m

hide_toggle()

In [47]:
m = prepareMap()
m

# Analisis Outliers

In [11]:
# SMC
Df_SMC_Total = pd.read_excel("finalsDF/DF_SMC.xlsx", index_col=0)
#['CC', 'CG', 'CI', 'CY', 'DG', 'DJ', 'DN', 'KE', 'UB', 'UN', 'UO', 'V3','V4', 'V5', 'VN', 'WS', 'DM_XJ_WF', 'Z4_ZC']

In [12]:
def calcularOutlier(df, col, cont=0.005):
    #Crear una versio horaria del dataset
    df['timestamp'] = pd.to_datetime(df.index)
    df = df.set_index('timestamp').resample("H").mean().reset_index()
    
    #Usem el metode de Isolation Forest per trobar anomalies a les precipitacions
    output = df[[col, 'timestamp']]
    temp = df[[col, 'timestamp']]
    model=IsolationForest(n_estimators=50, max_samples='auto', contamination=cont,max_features=1.0)
    model.fit(temp[[col]].values)
    output['outliers']=pd.Series(model.predict(temp[[col]].values)).apply(lambda x: 'yes' if (x == -1) else 'no' )
    
    return output

In [16]:
df = Df_SMC_Total
#Outliers de l'estacio meteorologica CC
cc = calcularOutlier(df, 'CC')


/var/folders/d4/kxqcphy54q9g3rr5tlcvhv9h0000gn/T/ipykernel_60869/1817129576.py:11: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [13]:
altTer = pd.read_excel("Dataframes/df_imputedAltTerKNN.xlsx", index_col=0)
baixTer = pd.read_excel("Dataframes/df_imputedBaixTerKNN.xlsx", index_col=0)

#Outliers de l'estacio de ACA més propera riu avall de l'estacio metereologica CC
#torrello = calcularOutlier(baixTer, "L17079-72-00005")


In [69]:
#Mostrar en un plot les anomalies que trobem amb la precipitació a CC i el cabal a torrelló de 2019 a 2022
cc = cc.loc[cc['timestamp'] >= '2019-01-01 00:00:00']
torrello = torrello.loc[torrello['timestamp'] >= '2019-01-01 00:00:00']
fig = px.scatter(cc, x='timestamp', y='CC', color='outliers',title='Outlier CC')
fig.update_xaxes(
    rangeslider_visible=True,
)
fig2 = px.scatter(torrello, x='timestamp', y='L17079-72-00005', color='outliers',title='Outlier Torrello')
fig2.update_xaxes(
    rangeslider_visible=True,
)
fig.show()
fig2.show()

Veiem que tenim al 23 de gener de 2020 una anomalia molt notable, al buscar aquesta data a Google més les paraules "riu ter inundacio" sorten noticias sobre com va haver-hi grans inundacions per la zona del baix Ter, per tant podem comprovar que aquesta anomalia va ocurrir realment i no es tracta d'un error tècnic.

Noticia: https://cat.elpais.com/cat/2020/01/23/catalunya/1579810582_789729.html

Al gràfic de l'estació CC veiem que a les dates de 22-23 de gener si va a haver-hi outliers, pero en cuant a m3/s no son tan desproprocionats amb la resta de valors comparat amb les dades de Torrelló. (Lo que si veiem es molta freqüencia de outliers, to-do: potser comprovar importancia de freqüencia de pluja, en lloc de plujes extremadament fortes?)

Anem a veure si una mica més riu a munt podem trobar anomalies per aquesta mateixa data

In [26]:
#Mirem una mica més amunt del riu, l'estacio meteorologica V4 i un altre cop l'estacio de ACA de torrelló

v4 = calcularOutlier(df, 'V4')
v4 = v4.loc[v4['timestamp'] >= '2019-01-01 00:00:00']
torrello = torrello.loc[torrello['timestamp'] >= '2019-01-01 00:00:00']
fig = px.scatter(v4, x='timestamp', y='V4', color='outliers',title='Outlier V4')
fig.update_xaxes(
    rangeslider_visible=True,
)
fig2 = px.scatter(torrello, x='timestamp', y='L17079-72-00005', color='outliers',title='Outlier Torrello', trendline='lowess')
fig2.update_xaxes(
    rangeslider_visible=True,
)
fig.show()
fig2.show()

/var/folders/d4/kxqcphy54q9g3rr5tlcvhv9h0000gn/T/ipykernel_60869/1817129576.py:11: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



Trobem dades molt similars amb l'estació metereologica CC, hi ha outliers a la mateixa data en la que van ocurrir les inundacions, pero la quantitat de pluja no es tan extremadament superior a la resta de outliers, como la quantitat de cabal durant aquesta data es a la resta de outliers. Lo que també veiem, es que van ocurrir les plujes amb molta frequencia durant aquesta data, mentre que a altres dies que també tenen outliers, els enregistraments d'aqusts outliers están més espaciats en el temps.

Mirem ara amb més detall durant la data que van haver-hi les inundacions, mirant també les dades de ACA a la part més amunt del riu i a la desembocadura.

In [9]:
start_date = widgets.DatePicker(
    description='Data Inici',
    disabled=False
)
end_date = widgets.DatePicker(
    description='Data Final',
    disabled=False
)

widgets.HBox([start_date, end_date])

In [18]:
cc = calcularOutlier(df, 'CC')
torrello = calcularOutlier(baixTer, "L17079-72-00005")
santJoan = calcularOutlier(altTer, "L17167-72-00001")
torroellaMontegri = calcularOutlier(baixTer, "L17199-72-00001")
v4 = calcularOutlier(df, 'V4')

/var/folders/d4/kxqcphy54q9g3rr5tlcvhv9h0000gn/T/ipykernel_60869/1817129576.py:11: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/var/folders/d4/kxqcphy54q9g3rr5tlcvhv9h0000gn/T/ipykernel_60869/1817129576.py:11: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/var/folders/d4/kxqcphy54q9g3rr5tlcvhv9h0000gn/T/ipykernel_60869/1817129576.py:11: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in th

In [22]:
start_date = pd.to_datetime(start_date.value)
end_date = pd.to_datetime(end_date.value)

cc = cc.loc[(cc['timestamp'] >= start_date) & (cc['timestamp'] <= end_date)]
v4 = v4.loc[(v4['timestamp'] >= start_date) &  (v4['timestamp'] <= end_date)]
torrello = torrello.loc[(torrello['timestamp'] >= start_date) & (torrello['timestamp'] <= end_date)]
santJoan = santJoan.loc[(santJoan['timestamp'] >= start_date) & (santJoan['timestamp'] <= end_date)]
torroellaMontegri = torroellaMontegri.loc[(torroellaMontegri['timestamp'] >= start_date) & (torroellaMontegri['timestamp'] <= end_date)]

fig = px.scatter(cc, x='timestamp', y='CC', color='outliers',title='Outlier CC')
fig.update_xaxes(
    rangeslider_visible=True,
)
fig2 = px.scatter(v4, x='timestamp', y='V4', color='outliers',title='Outlier V4')
fig2.update_xaxes(
    rangeslider_visible=True,
)
fig3 = px.scatter(santJoan, x='timestamp', y='L17167-72-00001', color='outliers',title='Outlier Sant Joan (Neixement)')
fig3.update_xaxes(
    rangeslider_visible=True,
)
fig4 = px.scatter(torrello, x='timestamp', y='L17079-72-00005', color='outliers',title='Outlier Torrello')
fig4.update_xaxes(
    rangeslider_visible=True,
)
fig5 = px.scatter(torroellaMontegri, x='timestamp', y='L17199-72-00001', color='outliers',title='Outlier Torroella-Montegri (Desembocadura)')
fig5.update_xaxes(
    rangeslider_visible=True,
)
fig.show()
fig2.show()
fig3.show()
fig4.show()
fig5.show()

Veiem que a totes les estacions del riu hi ha una pujada de cabal, seguida al dia seguent per una pujada encara mes gran. En canvi a la pluja es a l'inrevés, el primer dia plou més que al segon dia (on el cabal es més alt).

Anem a comprovar la pluja al neixement del riu.

In [46]:
start_date = pd.to_datetime(start_date.value)
end_date = pd.to_datetime(end_date.value)

cg = calcularOutlier(df, 'CG')
dg = calcularOutlier(df, 'DG')


cg = cg.loc[(cg['timestamp'] >= start_date) & (cg['timestamp'] <= end_date)]
dg = dg.loc[(dg['timestamp'] >= start_date) &  (dg['timestamp'] <= end_date)]

cg['CG'] = cg['CG'].rolling(window=5).mean()
dg['DG'] = dg['DG'].rolling(window=5).mean()

fig = px.scatter(cg, x='timestamp', y='CG', color='outliers',title='Outlier CG')
fig.update_xaxes(
    rangeslider_visible=True,
)
fig2 = px.scatter(dg, x='timestamp', y='DG', color='outliers',title='Outlier DG')
fig2.update_xaxes(
    rangeslider_visible=True,
)

fig.show()
fig2.show()

/var/folders/d4/kxqcphy54q9g3rr5tlcvhv9h0000gn/T/ipykernel_60869/1817129576.py:11: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/var/folders/d4/kxqcphy54q9g3rr5tlcvhv9h0000gn/T/ipykernel_60869/1817129576.py:11: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/var/folders/d4/kxqcphy54q9g3rr5tlcvhv9h0000gn/T/ipykernel_60869/2756019333.py:12: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in th

In [31]:
torrello

L17079-72-00005           timestamp outliers
96864         3.390000 2020-01-20 00:00:00       no
96865         3.359500 2020-01-20 01:00:00       no
96866         3.338000 2020-01-20 02:00:00       no
96867         3.308000 2020-01-20 03:00:00       no
96868         3.280000 2020-01-20 04:00:00       no
...                ...                 ...      ...
97004       157.799995 2020-01-25 20:00:00      yes
97005       156.500000 2020-01-25 21:00:00      yes
97006       151.750000 2020-01-25 22:00:00      yes
97007       150.400002 2020-01-25 23:00:00      yes
97008       150.800003 2020-01-26 00:00:00      yes

[145 rows x 3 columns]

In [32]:
cc

CC           timestamp outliers
96864  0.0 2020-01-20 00:00:00       no
96865  0.0 2020-01-20 01:00:00       no
96866  0.0 2020-01-20 02:00:00       no
96867  0.0 2020-01-20 03:00:00       no
96868  0.0 2020-01-20 04:00:00       no
...    ...                 ...      ...
97004  0.0 2020-01-25 20:00:00       no
97005  0.0 2020-01-25 21:00:00       no
97006  0.0 2020-01-25 22:00:00       no
97007  0.0 2020-01-25 23:00:00       no
97008  0.0 2020-01-26 00:00:00       no

[145 rows x 3 columns]

Utilitzem el metode de crosscorrelation per comprovar a partir de quin lag (en aquest cas diferencia de horas) hi ha més correlacio entre la pluja i el cabal

In [37]:
sm.tsa.stattools.ccf(cc['CC'], torrello['L17079-72-00005'], adjusted=False)

array([ 0.00389266, -0.03552576, -0.07152387, -0.10446644, -0.13233078,
       -0.15434399, -0.17570545, -0.20232923, -0.23199449, -0.25842606,
       -0.27395436, -0.28511637, -0.29036434, -0.28630264, -0.27285353,
       -0.25642753, -0.24539294, -0.24208481, -0.25433934, -0.27849232,
       -0.29748203, -0.31610696, -0.34145181, -0.3702248 , -0.39373687,
       -0.41106923, -0.42454955, -0.43801138, -0.44677053, -0.45348393,
       -0.45858948, -0.45204846, -0.4487326 , -0.44210278, -0.43670182,
       -0.43024152, -0.4205316 , -0.41375637, -0.40922735, -0.41252783,
       -0.41210393, -0.41055747, -0.40864291, -0.40544855, -0.39944145,
       -0.39318669, -0.3879314 , -0.37633569, -0.35818375, -0.34068467,
       -0.28879852, -0.26645236, -0.24739798, -0.22672591, -0.1972311 ,
       -0.18038619, -0.16613007, -0.14782978, -0.09135254, -0.05204962,
       -0.0271649 , -0.01692284, -0.005701  ,  0.00241309,  0.00798568,
        0.01395803,  0.0168898 ,  0.01959705,  0.0210483 ,  0.02

In [41]:
sm.tsa.stattools.ccf(santJoan['L17167-72-00001'], torrello['L17079-72-00005'], adjusted=False)

array([ 0.58337159,  0.52552138,  0.47289097,  0.42783194,  0.39138485,
        0.36407022,  0.34482783,  0.33123309,  0.32052829,  0.3095837 ,
        0.29655522,  0.28006258,  0.26130579,  0.24159144,  0.22228481,
        0.20511273,  0.19122806,  0.1796868 ,  0.16734878,  0.1523974 ,
        0.13288272,  0.10715187,  0.0757413 ,  0.04014699,  0.00173536,
       -0.03967027, -0.08287485, -0.12516471, -0.16519808, -0.20158952,
       -0.23349825, -0.26141307, -0.28587702, -0.30749166, -0.32708862,
       -0.34675683, -0.36667875, -0.38726369, -0.40847351, -0.4291575 ,
       -0.44713225, -0.4628748 , -0.47666776, -0.4889211 , -0.50068471,
       -0.51172348, -0.52252073, -0.53304092, -0.54138368, -0.54455071,
       -0.5402547 , -0.52947928, -0.51493133, -0.50008781, -0.4830362 ,
       -0.46422724, -0.44717574, -0.43109728, -0.41660664, -0.4027338 ,
       -0.39115658, -0.38166976, -0.37301168, -0.36415408, -0.35456889,
       -0.34523312, -0.33610116, -0.327119  , -0.31657208, -0.30